In [66]:
import numpy as np
import accelerate.cuda as cuda
import scipy

In [2]:
def rk4_step(x, f, dt):
    a = f(x)
    b = f(x+0.5*dt*a)
    c = f(x+0.5*dt*b)
    d = f(x+dt*c)
    return x+dt*(a+2*b+2*c+d)/6.0

def bmg(x):
    tmp = -1.0/(x[0]**2+x[1]**2)**(1.5)
    return np.array([x[2], x[3], x[0]*tmp, x[1]*tmp], dtype=np.double)

def E(x):
    return 0.5*(x[2]**2+x[3]**2)-1.0/np.sqrt(x[0]**2+x[1]**2)

In [3]:
dt   = 0.05
x0 = np.array([0, 4, 1.0/np.sqrt(10), 0], dtype=np.double)
max_iter = 2**20

In [4]:
x = x0
rx = [x[0]]
for i in range(max_iter):
    x = rk4_step(x, bmg, dt)
    rx.append(x[0])

In [5]:
len(rx)

1048577

### Converting rx(t) to complex typed array, because accelerate.cuda.fft likes complex input

In [35]:
x = np.array(rx, dtype=np.complex64)

In [36]:
Fx = np.zeros_like(x) #This will contain the result

## Initializing the cuda.FFT by creating FFTPlan

In [38]:
cuda.fft.FFTPlan(shape=x.shape, itype=np.complex64, otype=np.complex64)

## FFT

In [41]:
cuda.fft.fft(x, Fx);

## Visualization of result

In [43]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode()

# Hack for latex
from IPython.display import display, HTML
display(HTML(
    '<script>'
        'var waitForPlotly = setInterval( function() {'
            'if( typeof(window.Plotly) !== "undefined" ){'
                'MathJax.Hub.Config({ SVG: { font: "STIX-Web" }, displayAlign: "center" });'
                'MathJax.Hub.Queue(["setRenderer", MathJax.Hub, "SVG"]);'
                'clearInterval(waitForPlotly);'
            '}}, 250 );'
    '</script>'
))

In [45]:
absFx = np.absolute(Fx)

In [95]:
fig = go.Figure(
        data   = [go.Scatter(y=np.log(absFx[:70000]))], 
        layout = go.Layout(title='r$\mathcal{F}[x(t)]\; \mathrm{vs. index}$', 
                           xaxis=dict(title="$\mathrm{index}$"), 
                           yaxis=dict(title="$\mathcal{F}[x(t)]$$"))
    )

iplot(fig)

## First peak: 2112, this value corresponds to $2\pi/20$

In [84]:
omega = [2*np.pi/20/2112*i for i in range(60000)]

In [91]:
fig = go.Figure(
        data   = [go.Scatter(x=omega, y=np.log(absFx[:60000]))], 
        layout = go.Layout(title='r$\mathcal{F}[x(t)]\;\mathrm{vs.}\; \omega$', 
                           xaxis=dict(title="$\omega$"), 
                           yaxis=dict(title="$\mathcal{F}[x(t)]$"))
    )

iplot(fig)